Imran Muhammad, Olga Kellert, and Carlos Gómez-Rodríguez. "A Syntax-Injected Approach for Faster and More Accurate Sentiment Analysis." arXiv preprint arXiv:2406.15163 (2024). The preprint version is available on arXiv: URL: https://arxiv.org/html/2406.15163v1

### Install Libraries

In [1]:
!pip install matplotlib
!pip install datasets
!pip install easydict
!pip install frozendict
!pip install transformers
!pip install conllu
!pip install evaluate
!pip install seqeval
!pip install accelerate -U

### Import Libraries

In [20]:
import datasets
from datasets import Sequence, Value, ClassLabel, Features, load_dataset

from src.models.deps_tree import D_Tree
from src.models.deps_label import D_Label
from src.utils.constants import D_ROOT_HEAD, D_NULLHEAD, D_ROOT_REL, D_POSROOT, D_EMPTYREL, D_2P_GREED, D_2P_PROP
from src.encs.enc_deps import *
from src.utils.constants import *
from src.models.linearized_tree import LinearizedTree

import easydict
from frozendict import frozendict
import os
import torch
import pandas as pd
import numpy as np
import json
from tempfile import NamedTemporaryFile

from utilities import *
import transformers
from transformers import AutoTokenizer
from transformers import DataCollatorForTokenClassification
from transformers import AutoModelForTokenClassification, TrainingArguments, Trainer

import evaluate
import spacy

In [5]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

### Load Dataset

In [6]:
ud_path = "../datasets/UD_Spanish-AnCora/"
ud_path = os.path.expanduser(ud_path)

with open(os.path.join(ud_path,"es_ancora-ud-test.conllu")) as f:
    ud_test = [p.strip() for p in f.read().split('\n\n')]
with open(os.path.join(ud_path,"es_ancora-ud-dev.conllu")) as f:
    ud_dev = [p.strip() for p in f.read().split('\n\n')]
with open(os.path.join(ud_path,"es_ancora-ud-train.conllu")) as f:
    ud_train = [p.strip() for p in f.read().split('\n\n')]

In [7]:
print(ud_test[0])

# global.Entity = eid-etype-head-other
# newdoc id = 3LB-CAST-111_C-4
# sent_id = 3LB-CAST-111_C-4-s1
# text = Partidario de la "perestroika" de Mijail Gorbachov en la Unión Soviética, en 1989 entró en conflicto con Yívkov, líder durante 35 años del Partido Comunista y del Estado búlgaro, y le acusó en una carta abierta de utilizar métodos poco democráticos de gobierno.
# orig_file_sentence 001#1
1	Partidario	partidario	ADJ	aq0ms0	Gender=Masc|Number=Sing	17	amod	17:amod	_
2	de	de	ADP	sps00	_	5	case	5:case	_
3	la	el	DET	da0fs0	Definite=Def|Gender=Fem|Number=Sing|PronType=Art	5	det	5:det	Entity=(NOCOREF:Spec.other-other-3-gstype:spec
4	"	"	PUNCT	fe	PunctType=Quot	5	punct	5:punct	SpaceAfter=No
5	perestroika	perestroika	NOUN	ncfs000	Gender=Fem|Number=Sing	1	nmod	1:nmod	SpaceAfter=No
6	"	"	PUNCT	fe	PunctType=Quot	5	punct	5:punct	_
7	de	de	ADP	sps00	_	8	case	8:case	_
8	Mijail	Mijail	PROPN	np0000p	_	5	nmod	5:nmod	MWE=Mijail_Gorbachov|MWEPOS=PROPN|Entity=(NOCOREF:Spec.person-person-1-gstype:sp

### Decode UD Treebank using CoDeLin Library

In [8]:
def encode(conllu_samples):
    samples = []
    for conllu_sample in conllu_samples:
        d_tree = D_Tree.from_string(conllu_sample)
        encoder = D_NaiveRelativeEncoding(separator="_", hang_from_root=True)
        ld_tree = encoder.encode(d_tree)
        samples.append(remove_bos_eos_tags(ld_tree))
    return samples

def remove_bos_eos_tags(text):
    sentence = text.to_string()
    lines = sentence.split('\n')
    lines = lines[1:-2]
    sentence = '\n'.join(lines)
    return sentence

In [9]:
ud_test_original = ud_test
ud_test = encode(ud_test)
ud_dev = encode(ud_dev)
ud_train = encode(ud_train)

print(ud_test[0])

Partidario	ADJ	16_amod
de	ADP	3_case
la	DET	2_det
"	PUNCT	1_punct
perestroika	NOUN	-4_nmod
"	PUNCT	-1_punct
de	ADP	1_case
Mijail	PROPN	-3_nmod
Gorbachov	PROPN	-1_flat
en	ADP	2_case
la	DET	1_det
Unión	PROPN	-7_nmod
Soviética	PROPN	-1_flat
,	PUNCT	-13_punct
en	ADP	1_case
1989	NOUN	1_obl
entró	VERB	-NONE-_root
en	ADP	1_case
conflicto	NOUN	-2_obl
con	ADP	1_case
Yívkov	PROPN	-4_obl
,	PUNCT	1_punct
líder	NOUN	-2_appos
durante	ADP	2_case
35	NUM	1_nummod
años	NOUN	-3_nmod
de	ADP	2_case
el	DET	1_det
Partido	PROPN	-6_nmod
Comunista	PROPN	-1_flat
y	CCONJ	3_cc
de	ADP	2_case
el	DET	1_det
Estado	PROPN	-5_conj
búlgaro	ADJ	-1_amod
,	PUNCT	3_punct
y	CCONJ	2_cc
le	PRON	1_obl:arg
acusó	VERB	-22_conj
en	ADP	2_case
una	DET	1_det
carta	NOUN	-3_obl
abierta	ADJ	-1_amod
de	ADP	1_mark
utilizar	VERB	-6_xcomp
métodos	NOUN	-1_obj
poco	ADV	1_advmod
democráticos	ADJ	-2_amod
de	ADP	1_case
gobierno	NOUN	-4_nmod
.	PUNCT	-34_punct


In [13]:
def return_class_names(data_files):
    train_file = data_files["train"]
    eval_file = data_files["validation"]
    test_file = data_files["test"]

    class_names = {"pos_tags": set(), "syntax_labels": set()}

    for file in [train_file, eval_file, test_file]:
        for sentence in file:
            #sentence = sentence.to_string()
            sentence = str(sentence)
            lines = sentence.split('\n')
            for line in lines:
                if line:
                    token, pos_tag, syntax_label = line.split('\t')
                    class_names["pos_tags"].add(pos_tag)
                    if file != test_file:
                        class_names["syntax_labels"].add(syntax_label)

    class_names["pos_tags"] = list(class_names["pos_tags"])
    class_names["syntax_labels"] = list(class_names["syntax_labels"])

    # add UNK label
    class_names["syntax_labels"].append("UNK")

    return class_names

In [14]:
def create_json_files(data_files):
    """Convert the TSV data files in a JSON file to create a dataset"""
    train_json = NamedTemporaryFile("w", delete=False)
    eval_json = NamedTemporaryFile("w", delete=False)
    test_json = NamedTemporaryFile("w", delete=False) 

    train_list = []
    eval_list = []
    test_list = []
    
    class_names = return_class_names(data_files)

    for split in data_files:
        idx = 0
        file = data_files[split]
            
        for sentence in file:
            idx += 1
            sentence_tokens = []
            sentence_pos_tags = []
            sentence_syntax_labels = []
            sentence = str(sentence)
            lines = sentence.split('\n')
            
            if len(lines) > 1:
                for line in lines:
                    if line:
                        token, pos_tag, syntax_label = line.split('\t')
                        sentence_tokens.append(token)
                        sentence_pos_tags.append(pos_tag)
                        if split != "test":
                            sentence_syntax_labels.append(syntax_label)
                        else:
                            if syntax_label in class_names["syntax_labels"]:
                                sentence_syntax_labels.append(syntax_label)
                            else:
                                sentence_syntax_labels.append("UNK")

            if sentence_tokens != []:
                if split == "train":
                    train_list.append({"id": idx, "tokens": sentence_tokens, "pos_tags": sentence_pos_tags, "syntax_labels": sentence_syntax_labels})
                elif split == "validation":
                    eval_list.append({"id": idx, "tokens": sentence_tokens, "pos_tags": sentence_pos_tags, "syntax_labels": sentence_syntax_labels})
                else:
                    test_list.append({"id": idx, "tokens": sentence_tokens, "pos_tags": sentence_pos_tags, "syntax_labels": sentence_syntax_labels})

    train_dic = {"data": train_list}
    eval_dic = {"data": eval_list}
    test_dic = {"data": test_list}

    with open(train_json.name, 'w', encoding='utf-8') as f:
        json.dump(train_dic, f, ensure_ascii=False)

    with open(eval_json.name, 'w', encoding='utf-8') as f:
        json.dump(eval_dic, f, ensure_ascii=False)
    
    with open(test_json.name, 'w', encoding='utf-8') as f:
        json.dump(test_dic, f, ensure_ascii=False)

    return {"train":train_json.name, "validation":eval_json.name, "test":test_json.name}

In [15]:
seqeval = evaluate.load("seqeval")

def compute_metrics(eval_preds):
    logits, labels = eval_preds
    predictions = np.argmax(logits, axis=-1)

    # Remove ignored index (special tokens) and convert to labels
    true_labels = [[label_names[l] for l in label if l != -100] for label in labels]
    true_predictions = [
        [label_names[p] for (p, l) in zip(prediction, label) if l != -100]
        for prediction, label in zip(predictions, labels)
    ]
    all_metrics = seqeval.compute(predictions=true_predictions, references=true_labels)
    return {
        "precision": all_metrics["overall_precision"],
        "recall": all_metrics["overall_recall"],
        "f1": all_metrics["overall_f1"],
        "accuracy": all_metrics["overall_accuracy"],
    }

In [16]:
data_dir = 'data/const/single/distilbert-base-spanish-uncased/spanish/'

data_tsv = {
    "train": ud_train, 
    "validation": ud_dev,
    "test": ud_test
}

data_json = create_json_files(data_tsv)
class_names = return_class_names(data_tsv)

num_labels = len(class_names["syntax_labels"])

label2id = {v: i for i, v in enumerate(class_names["syntax_labels"])}
id2label = {i: v for i, v in enumerate(class_names["syntax_labels"])}

### Initialize Model From Pretrained Checkpoint

In [18]:
# Initilize Pretrained Model
model = AutoModelForTokenClassification.from_pretrained(
    "dccuchile/distilbert-base-spanish-uncased", # dccuchile/distilbert-base-spanish-uncased  for spanish datasets
    num_labels=num_labels,
    id2label=id2label,
    label2id=label2id
)

# Initilize Tokenizer for Pretrained Model
tokenizer = AutoTokenizer.from_pretrained("dccuchile/distilbert-base-spanish-uncased", add_prefix_space=True)
data_collator = DataCollatorForTokenClassification(tokenizer=tokenizer)

dataset = load_dataset(
    "json",
    data_files=data_json,
    features=Features(
        {
            "id": Value("int64"),
            "tokens": Sequence(Value("string")),
            "pos_tags": Sequence(ClassLabel(names=class_names["pos_tags"], num_classes=len(class_names["pos_tags"]))),
            "syntax_labels": Sequence(ClassLabel(names=class_names["syntax_labels"], num_classes=len(class_names["syntax_labels"]))),
        }
    ),
    field="data"
)

syntax_features = dataset["train"].features["syntax_labels"]
label_names = syntax_features.feature.names

# Align Tokens and Labels
dataset = dataset.map(
    tokenize_and_align_labels, 
    batched=True,
    remove_columns=dataset["train"].column_names,
    fn_kwargs={"tokenizer": tokenizer})

# Save Tokenized Dataset to the Disk
dataset.save_to_disk('models/rel-distilbert-es/dataset')

features = dataset["train"].features["labels"]

# Model Hyperparameters
training_args = TrainingArguments(
    "spanish-distilbert-v1/model",
    per_device_train_batch_size=128,
    learning_rate=1e-4,
    num_train_epochs= 30,
    weight_decay=0.001,
    adam_epsilon= 1e-7,
    adam_beta1= 0.9,
    adam_beta2= 0.999,
    metric_for_best_model="f1",  # Choose "f1" as the metric to evaluate the best model
    greater_is_better=True, 
    evaluation_strategy = "epoch",
    save_strategy="epoch",
    #save_strategy = "no",
    load_best_model_at_end=True,
)

# Initilize Model Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=dataset["train"],
    eval_dataset=dataset["validation"],
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    tokenizer=tokenizer,
)

# Train the Model
trainer.train()
# Save Trained Model
trainer.save_model('models/rel-distilbert-es/model')

Some weights of DistilBertForTokenClassification were not initialized from the model checkpoint at dccuchile/distilbert-base-spanish-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Extracting data files:   0%|          | 0/3 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

...

Map:   0%|          | 0/1721 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/14286 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/1654 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/1721 [00:00<?, ? examples/s]

You're using a DistilBertTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


### Inference with Raw Text (not tokenized)

In [19]:
from transformers import AutoTokenizer

text = 'Partidario de la "perestroika" de Mijail Gorbachov en la Unión Soviética, en 1989 entró en conflicto con Yívkov, líder durante 35 años del Partido Comunista y del Estado búlgaro, y le acusó en una carta abierta de utilizar métodos poco democráticos de gobierno.'
tokenizer = AutoTokenizer.from_pretrained("dccuchile/distilbert-base-spanish-uncased")
inputs = tokenizer(text, return_tensors="pt")
print(inputs)

input_srts = tokenizer.convert_ids_to_tokens(inputs['input_ids'][0])
print(input_srts)

decoded_string = tokenizer.decode(inputs['input_ids'][0])
decoded_string = decoded_string.split()
decoded_string = " ".join(decoded_string[1:-1])
print(decoded_string)

model = AutoModelForTokenClassification.from_pretrained("models/rel-distilbert-es/model")
with torch.no_grad():
    logits = model(**inputs).logits
    #logits = model(input_ids).logits
    
predictions = torch.argmax(logits, dim=2)
predicted_token_class = [model.config.id2label[t.item()] for t in predictions[0][1:-1]]
#raw predictied by the model
print(predicted_token_class)

Partidario de la "perestroika" de Mijail Gorbachov en la Unión Soviética, en 1989 entró en conflicto con Yívkov, líder durante 35 años del Partido Comunista y del Estado búlgaro, y le acusó en una carta abierta de utilizar métodos poco democráticos de gobierno.
{'input_ids': tensor([[    4, 25562,  1009,  1032,  1100,  9942,  8689,  1053, 17691,  1100,
          1009,  1136,  1431,  1123,  4787, 18428,  5129,  1035,  1032,  2656,
          9017,  1019,  1035,  1220,   996, 30995,  6300,  1035,  5170,  1048,
          1040, 27373,  9368,  1019,  4537,  1672,  4171,  1469,  1081,  2887,
          9994,  1040,  1081,  1520, 28961,  1019,  1040,  1165, 22543,  1035,
          1091,  3350,  6051,  1009,  4917,  5649,  1819, 20821,  1009,  2022,
          1008,     5]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,

### Inference with Pre-tokenized Text

In [21]:
# Example raw text/data
text = 'Partidario de la "perestroika" de Mijail Gorbachov en la Unión Soviética, en 1989 entró en conflicto con Yívkov, líder durante 35 años del Partido Comunista y del Estado búlgaro, y le acusó en una carta abierta de utilizar métodos poco democráticos de gobierno.'
tokens_with_spacy = get_tokens_by_spacy(text)
print(tokens_with_spacy)

tokenized_text = pre_tokenized_text(tokens_with_spacy)
# Example pre-tokenized text/data
#tokenized_text = ["[CLS]", 'I', 'do', "n't", 'eat', 'very', 'much', 'pieces', 'of', 'chocolate', '.', "[SEP]"]

# Convert tokens to input IDs using the tokenizer
tokenizer = AutoTokenizer.from_pretrained("dccuchile/distilbert-base-spanish-uncased")
input_ids = tokenizer.convert_tokens_to_ids(tokenized_text)

# Create input tensors
input_ids = torch.tensor(input_ids).unsqueeze(0)  # Add a batch dimension

model = AutoModelForTokenClassification.from_pretrained("spanish-distilbert-v1/model")
with torch.no_grad():
    #logits = model(**inputs).logits
    logits = model(input_ids).logits
    
    predictions = torch.argmax(logits, dim=2)
    predicted_token_class = [model.config.id2label[t.item()] for t in predictions[0][1:-1]]
    # Model's predictions/rules
    print(predicted_token_class)

['Partidario', 'de', 'la', '"', 'perestroika', '"', 'de', 'Mijail', 'Gorbachov', 'en', 'la', 'Unión', 'Soviética', ',', 'en', '1989', 'entró', 'en', 'conflicto', 'con', 'Yívkov', ',', 'líder', 'durante', '35', 'años', 'del', 'Partido', 'Comunista', 'y', 'del', 'Estado', 'búlgaro', ',', 'y', 'le', 'acusó', 'en', 'una', 'carta', 'abierta', 'de', 'utilizar', 'métodos', 'poco', 'democráticos', 'de', 'gobierno', '.']
['18_nsubj', '3_case', '2_det', '1_punct', '-4_nmod', '-1_punct', '1_case', '-3_nmod', '-1_flat', '2_case', '1_det', '-6_nmod', '-1_flat', '-11_punct', '1_case', '1_obl', '-NONE-_root', '1_case', '-2_obl', '1_case', '-2_nmod', '1_punct', '-2_appos', '2_case', '1_nummod', '-3_nmod', '1_case', '-5_nmod', '-1_flat', '2_cc', '1_det', '-4_conj', '-1_flat', '3_punct', '2_cc', '1_obl:arg', '-20_conj', '2_case', '1_det', '-3_obl', '-1_amod', '1_mark', '-6_ccomp', '-1_obj', '1_advmod', '-2_amod', '1_case', '-2_nmod', '-37_punct']


### Decoded Inference Trees or Predictions from the Model on Test Dataset

In [22]:
test_trees = ud_test_original
dec_trees = []
tree_cycles_ids = []
tree_cycles = []
with torch.no_grad():
    for idx, gold_tree in enumerate(test_trees):
        tree = D_Tree.from_string(gold_tree)
        
        words = tree.get_words()
        words = words[1:]
        postags = tree.get_postags()
        postags = postags[1:]
        sentence = " ".join(words)
        sentence = sentence.strip()
        sentence = sentence.lower()
        print(sentence)
        
        tokenized_text = pre_tokenized_text(words)
        # Convert tokens to input IDs using the tokenizer
        tokenizer = AutoTokenizer.from_pretrained("dccuchile/distilbert-base-spanish-uncased")
        input_ids = tokenizer.convert_tokens_to_ids(tokenized_text)

        # Create input tensors
        input_ids = torch.tensor(input_ids).unsqueeze(0)  # Add a batch dimension
        output = model(input_ids)
        logits = output.logits
        predictions = torch.argmax(logits, dim=2)
        true_predictions = [model.config.id2label[t.item()] for t in predictions[0][1:-1]]

        labels = []
        for p in true_predictions:
            if(p != '[CLS]' and p != '[SEP]'):
                labels.append(D_Label.from_string(p, sep="_"))
        
        lin_tree = LinearizedTree(words=words, postags=postags,
                    additional_feats=[], labels=labels, n_feats=0)
        
        encoder = D_NaiveRelativeEncoding(separator="_", hang_from_root=True)
        dec_tree = encoder.decode(lin_tree)
        dec_tree.postprocess_tree(search_root_strat=D_ROOT_HEAD, allow_multi_roots=False)
        dec_tree = str(dec_tree)
        dec_trees.append(dec_tree)
        print(dec_tree)
        
        # Localize sentences having "UD Error: There is a cycle in a sentence"
        if "root" not in dec_tree:
            tree_cycles_ids.append(idx)
            tree_cycles.append(dec_tree)

partidario de la " perestroika " de mijail gorbachov en la unión soviética , en 1989 entró en conflicto con yívkov , líder durante 35 años de el partido comunista y de el estado búlgaro , y le acusó en una carta abierta de utilizar métodos poco democráticos de gobierno .
1	Partidario	_	ADJ	_	_	19	nsubj	_	_
2	de	_	ADP	_	_	5	case	_	_
3	la	_	DET	_	_	5	det	_	_
4	"	_	PUNCT	_	_	5	punct	_	_
5	perestroika	_	NOUN	_	_	1	nmod	_	_
6	"	_	PUNCT	_	_	5	punct	_	_
7	de	_	ADP	_	_	8	case	_	_
8	Mijail	_	PROPN	_	_	5	nmod	_	_
9	Gorbachov	_	PROPN	_	_	8	flat	_	_
10	en	_	ADP	_	_	12	case	_	_
11	la	_	DET	_	_	12	det	_	_
12	Unión	_	PROPN	_	_	6	nmod	_	_
13	Soviética	_	PROPN	_	_	12	flat	_	_
14	,	_	PUNCT	_	_	3	punct	_	_
15	en	_	ADP	_	_	16	case	_	_
16	1989	_	NOUN	_	_	17	obl	_	_
17	entró	_	VERB	_	_	0	root	_	_
18	en	_	ADP	_	_	19	case	_	_
19	conflicto	_	NOUN	_	_	17	obl	_	_
20	con	_	ADP	_	_	21	case	_	_
21	Yívkov	_	PROPN	_	_	19	nmod	_	_
22	,	_	PUNCT	_	_	23	punct	_	_
23	líder	_	NOUN	_	_	21	appos	_	_
24	durante	_	ADP	_	_	26	c

1	"	_	PUNCT	_	_	5	punct	_	_
2	El	_	DET	_	_	3	det	_	_
3	Gobierno	_	PROPN	_	_	5	nsubj	_	_
4	chino	_	ADJ	_	_	3	amod	_	_
5	respeta	_	VERB	_	_	26	ccomp	_	_
6	la	_	DET	_	_	7	det	_	_
7	decisión	_	NOUN	_	_	5	obj	_	_
8	de	_	ADP	_	_	10	case	_	_
9	el	_	DET	_	_	10	det	_	_
10	pueblo	_	NOUN	_	_	7	nmod	_	_
11	peruano	_	ADJ	_	_	10	amod	_	_
12	expresada	_	ADJ	_	_	7	amod	_	_
13	en	_	ADP	_	_	16	case	_	_
14	la	_	DET	_	_	16	det	_	_
15	segunda	_	ADJ	_	_	16	amod	_	_
16	ronda	_	NOUN	_	_	12	obl	_	_
17	de	_	ADP	_	_	19	case	_	_
18	las	_	DET	_	_	19	det	_	_
19	elecciones	_	NOUN	_	_	16	nmod	_	_
20	el	_	DET	_	_	22	det	_	_
21	pasado	_	NOUN	_	_	22	amod	_	_
22	domingo	_	NOUN	_	_	11	obl	_	_
23	"	_	PUNCT	_	_	4	punct	_	_
24	,	_	PUNCT	_	_	4	punct	_	_
25	declaró	_	VERB	_	_	0	root	_	_
26	esta	_	DET	_	_	27	det	_	_
27	tarde	_	NOUN	_	_	25	obl	_	_
28	Zhang	_	PROPN	_	_	25	nsubj	_	_
29	Qiyue	_	PROPN	_	_	28	flat	_	_
30	,	_	PUNCT	_	_	31	punct	_	_
31	portavoz	_	NOUN	_	_	28	appos	_	_
32	de	_	ADP	_	_	34	case	_	_
33	la	_	DET	_	_	34	det	

1	Además	_	ADV	_	_	6	advmod	_	_
2	,	_	PUNCT	_	_	1	punct	_	_
3	estas	_	DET	_	_	5	det	_	_
4	dos	_	NUM	_	_	3	nummod	_	_
5	naciones	_	NOUN	_	_	6	nsubj	_	_
6	tienen	_	VERB	_	_	0	root	_	_
7	una	_	DET	_	_	9	det	_	_
8	larga	_	ADJ	_	_	9	amod	_	_
9	historia	_	NOUN	_	_	6	obj	_	_
10	de	_	ADP	_	_	11	case	_	_
11	relaciones	_	NOUN	_	_	9	nmod	_	_
12	,	_	PUNCT	_	_	22	punct	_	_
13	desde	_	ADP	_	_	22	mark	_	_
14	que	_	SCONJ	_	_	21	mark	_	_
15	,	_	PUNCT	_	_	16	punct	_	_
16	hace	_	VERB	_	_	21	advcl	_	_
17	150	_	NUM	_	_	18	nummod	_	_
18	años	_	NOUN	_	_	16	obj	_	_
19	,	_	PUNCT	_	_	18	punct	_	_
20	se	_	PRON	_	_	21	expl:pv	_	_
21	produjera	_	VERB	_	_	5	advcl	_	_
22	la	_	DET	_	_	24	det	_	_
23	primera	_	ADJ	_	_	24	amod	_	_
24	migración	_	NOUN	_	_	21	nsubj	_	_
25	china	_	ADJ	_	_	24	amod	_	_
26	a	_	ADP	_	_	28	case	_	_
27	el	_	DET	_	_	28	det	_	_
28	Perú	_	PROPN	_	_	24	nmod	_	_
29	.	_	PUNCT	_	_	5	punct	_	_


hace escasamente un mes , el canciller peruano , fernando de trazegnies , viajó a pekín en visita oficial par

1	-	_	PUNCT	_	_	3	punct	_	_
2	Se	_	PRON	_	_	3	expl:pv	_	_
3	acuerdan	_	VERB	_	_	0	root	_	_
4	ustedes	_	PRON	_	_	3	nsubj	_	_
5	de	_	ADP	_	_	6	case	_	_
6	eso	_	PRON	_	_	3	nmod	_	_
7	que	_	PRON	_	_	9	nsubj	_	_
8	se	_	PRON	_	_	9	expl:pv	_	_
9	llamaba	_	VERB	_	_	4	acl	_	_
10	la	_	DET	_	_	11	det	_	_
11	voz	_	NOUN	_	_	9	obj	_	_
12	de	_	ADP	_	_	14	case	_	_
13	la	_	DET	_	_	14	det	_	_
14	conciencia	_	NOUN	_	_	11	flat	_	_
15	?	_	PUNCT	_	_	2	punct	_	_


yo tardé mucho tiempo en enterar me de que no había tal voz , de que se trataba sólo de una vieja metáfora , y como nunca lograba escuchar a nadie que hablara dentro de mí me mantuve durante bastantes años en un estado de feliz inconsciencia .
1	Yo	_	PRON	_	_	2	nsubj	_	_
2	tardé	_	VERB	_	_	0	root	_	_
3	mucho	_	DET	_	_	4	det	_	_
4	tiempo	_	NOUN	_	_	2	obj	_	_
5	en	_	ADP	_	_	6	mark	_	_
6	enterar	_	VERB	_	_	2	advcl	_	_
7	me	_	PRON	_	_	6	expl:pv	_	_
8	de	_	ADP	_	_	11	mark	_	_
9	que	_	SCONJ	_	_	11	mark	_	_
10	no	_	ADV	_	_	11	advmod	_	_
11	había	_	VERB	_	

1	Lo	_	PRON	_	_	3	obj	_	_
2	suyo	_	DET	_	_	3	nsubj	_	_
3	es	_	AUX	_	_	0	root	_	_
4	vivir	_	VERB	_	_	3	ccomp	_	_
5	junto	_	ADJ	_	_	8	case	_	_
6	a	_	ADP	_	_	5	fixed	_	_
7	la	_	DET	_	_	8	det	_	_
8	gente	_	NOUN	_	_	4	obl	_	_
9	fina	_	ADJ	_	_	8	amod	_	_
10	,	_	PUNCT	_	_	12	punct	_	_
11	que	_	PRON	_	_	12	nsubj	_	_
12	come	_	VERB	_	_	8	acl	_	_
13	sólo	_	ADV	_	_	15	advmod	_	_
14	la	_	DET	_	_	15	det	_	_
15	mitad	_	NOUN	_	_	12	obj	_	_
16	de	_	ADP	_	_	19	mark	_	_
17	lo	_	PRON	_	_	19	det	_	_
18	que	_	PRON	_	_	19	obj	_	_
19	compra	_	VERB	_	_	15	acl	_	_
20	.	_	PUNCT	_	_	3	punct	_	_


dicen que en los países más prósperos y desarrollados viven ya tantas ratas como seres humanos , y en algunos incluso más .
1	Dicen	_	VERB	_	_	0	root	_	_
2	que	_	SCONJ	_	_	9	mark	_	_
3	en	_	ADP	_	_	5	case	_	_
4	los	_	DET	_	_	5	det	_	_
5	países	_	NOUN	_	_	9	obl	_	_
6	más	_	ADV	_	_	7	advmod	_	_
7	prósperos	_	ADJ	_	_	5	nmod	_	_
8	y	_	CCONJ	_	_	9	cc	_	_
9	desarrollados	_	ADJ	_	_	1	conj	_	_
10	viven	_	VERB	_	_	2	ccomp	_	_
11

...

1	Su	_	DET	_	_	2	det	_	_
2	laboratorio	_	NOUN	_	_	18	nsubj	_	_
3	,	_	PUNCT	_	_	4	punct	_	_
4	Instituto	_	PROPN	_	_	2	appos	_	_
5	Municipal	_	PROPN	_	_	4	flat	_	_
6	de	_	ADP	_	_	7	case	_	_
7	Investigación	_	PROPN	_	_	4	flat	_	_
8	Médica	_	PROPN	_	_	7	flat	_	_
9	(	_	PUNCT	_	_	10	punct	_	_
10	IMIM-IMAS	_	PROPN	_	_	5	flat	_	_
11	)	_	PUNCT	_	_	10	punct	_	_
12	,	_	PUNCT	_	_	13	punct	_	_
13	reconocido	_	ADJ	_	_	6	amod	_	_
14	por	_	ADP	_	_	16	case	_	_
15	el	_	DET	_	_	16	det	_	_
16	COI	_	PROPN	_	_	13	obl:agent	_	_
17	,	_	PUNCT	_	_	13	punct	_	_
18	goza	_	VERB	_	_	0	root	_	_
19	,	_	PUNCT	_	_	20	punct	_	_
20	también	_	ADV	_	_	18	advmod	_	_
21	,	_	PUNCT	_	_	20	punct	_	_
22	de	_	ADP	_	_	25	case	_	_
23	una	_	DET	_	_	25	det	_	_
24	enorme	_	ADJ	_	_	25	amod	_	_
25	fama	_	NOUN	_	_	18	obl:arg	_	_
26	internacional	_	ADJ	_	_	25	amod	_	_
27	.	_	PUNCT	_	_	17	punct	_	_


segura estuvo presente , como experto en la materia , en los juegos de salt lake .
1	Segura	_	PROPN	_	_	3	nsubj	_	_
2	estuvo	_	AUX	_	_	1	cop	

1	Ahora	_	ADV	_	_	3	advmod	_	_
2	Arafat	_	PROPN	_	_	3	nsubj	_	_
3	está	_	VERB	_	_	0	root	_	_
4	entre	_	ADP	_	_	6	case	_	_
5	sus	_	DET	_	_	6	det	_	_
6	gentes	_	NOUN	_	_	3	obl	_	_
7	.	_	PUNCT	_	_	3	punct	_	_


a pesar de los sufrimientos , ellos no exigirán su marcha .
1	A	_	ADP	_	_	5	case	_	_
2	pesar	_	NOUN	_	_	1	fixed	_	_
3	de	_	ADP	_	_	1	fixed	_	_
4	los	_	DET	_	_	5	det	_	_
5	sufrimientos	_	NOUN	_	_	10	obl	_	_
6	,	_	PUNCT	_	_	5	punct	_	_
7	ellos	_	PRON	_	_	9	nsubj	_	_
8	no	_	ADV	_	_	9	advmod	_	_
9	exigirán	_	VERB	_	_	0	root	_	_
10	su	_	DET	_	_	11	det	_	_
11	marcha	_	NOUN	_	_	9	obj	_	_
12	.	_	PUNCT	_	_	8	punct	_	_


por lo tanto israel quiere eliminar le política o físicamente para crear una situación caótica .
1	Por	_	ADP	_	_	5	advmod	_	_
2	lo	_	PRON	_	_	1	fixed	_	_
3	tanto	_	NOUN	_	_	1	fixed	_	_
4	Israel	_	PROPN	_	_	5	nsubj	_	_
5	quiere	_	VERB	_	_	0	root	_	_
6	eliminar	_	VERB	_	_	5	xcomp	_	_
7	le	_	PRON	_	_	6	obj	_	_
8	política	_	ADV	_	_	6	obj	_	_
9	o	_	CCONJ	_	_	10	cc	_	_
10	físicame

1	Tres	_	NUM	_	_	2	nummod	_	_
2	heridos	_	NOUN	_	_	5	nsubj	_	_
3	fueron	_	AUX	_	_	5	aux	_	_
4	ayer	_	ADV	_	_	5	advmod	_	_
5	dados	_	VERB	_	_	0	root	_	_
6	de	_	ADP	_	_	5	advmod	_	_
7	alta	_	NOUN	_	_	6	fixed	_	_
8	,	_	PUNCT	_	_	14	punct	_	_
9	por	_	ADP	_	_	14	mark	_	_
10	lo	_	PRON	_	_	14	det	_	_
11	que	_	PRON	_	_	14	obl	_	_
12	35	_	NUM	_	_	13	nummod	_	_
13	personas	_	NOUN	_	_	14	nsubj	_	_
14	permanecían	_	VERB	_	_	5	advcl	_	_
15	anoche	_	ADV	_	_	14	advmod	_	_
16	ingresadas	_	ADJ	_	_	13	obj	_	_
17	en	_	ADP	_	_	18	case	_	_
18	hospitales	_	NOUN	_	_	13	obl	_	_
19	de	_	ADP	_	_	20	case	_	_
20	Tarragona	_	PROPN	_	_	18	nmod	_	_
21	,	_	PUNCT	_	_	22	punct	_	_
22	Reus	_	PROPN	_	_	20	conj	_	_
23	,	_	PUNCT	_	_	24	punct	_	_
24	Valls	_	PROPN	_	_	20	conj	_	_
25	,	_	PUNCT	_	_	26	punct	_	_
26	Viladecans	_	PROPN	_	_	20	conj	_	_
27	,	_	PUNCT	_	_	28	punct	_	_
28	Martorell	_	PROPN	_	_	20	conj	_	_
29	,	_	PUNCT	_	_	30	punct	_	_
30	Ontinyent	_	PROPN	_	_	22	conj	_	_
31	,	_	PUNCT	_	_	32	punct	_	_
32	Madrid	_	PROPN

1	El	_	DET	_	_	2	det	_	_
2	juego	_	NOUN	_	_	4	nsubj	_	_
3	se	_	PRON	_	_	4	expl:pass	_	_
4	comercializa	_	VERB	_	_	0	root	_	_
5	para	_	ADP	_	_	6	case	_	_
6	Gameboy	_	PROPN	_	_	4	obl	_	_
7	Advance	_	PROPN	_	_	6	punct	_	_
8	(	_	PUNCT	_	_	13	punct	_	_
9	que	_	PRON	_	_	13	nsubj	_	_
10	es	_	AUX	_	_	13	cop	_	_
11	la	_	DET	_	_	13	det	_	_
12	nueva	_	ADJ	_	_	13	amod	_	_
13	consola	_	NOUN	_	_	6	acl	_	_
14	de	_	ADP	_	_	15	case	_	_
15	bolsillo	_	NOUN	_	_	13	nmod	_	_
16	de	_	ADP	_	_	17	case	_	_
17	Nintendo	_	PROPN	_	_	13	nmod	_	_
18	,	_	PUNCT	_	_	19	punct	_	_
19	sensación	_	NOUN	_	_	14	amod	_	_
20	de	_	ADP	_	_	23	case	_	_
21	todos	_	DET	_	_	22	det	_	_
22	los	_	DET	_	_	23	det	_	_
23	adolescentes	_	NOUN	_	_	19	nmod	_	_
24	y	_	CCONJ	_	_	25	cc	_	_
25	niños	_	NOUN	_	_	23	conj	_	_
26	)	_	PUNCT	_	_	11	punct	_	_
27	,	_	PUNCT	_	_	29	punct	_	_
28	para	_	ADP	_	_	29	case	_	_
29	Playstation	_	PROPN	_	_	14	nmod	_	_
30	2	_	NUM	_	_	29	nummod	_	_
31	y	_	CCONJ	_	_	33	cc	_	_
32	para	_	ADP	_	_	33	case	_	_
33	PC	_	PROPN

1	La	_	DET	_	_	2	det	_	_
2	emisora	_	NOUN	_	_	6	nsubj	_	_
3	de	_	ADP	_	_	4	case	_	_
4	Radio	_	PROPN	_	_	2	nmod	_	_
5	Liberty	_	PROPN	_	_	4	flat	_	_
6	vuelve	_	VERB	_	_	0	root	_	_
7	a	_	ADP	_	_	8	case	_	_
8	RNE	_	PROPN	_	_	6	obl	_	_
9	.	_	PUNCT	_	_	6	punct	_	_


el gobierno de estados unidos transfirió ayer formalmente la emisora de radio liberty a radio nacional de españa , que ahora gestiona la instalación .
1	El	_	DET	_	_	2	det	_	_
2	Gobierno	_	PROPN	_	_	6	nsubj	_	_
3	de	_	ADP	_	_	4	case	_	_
4	Estados	_	PROPN	_	_	2	nmod	_	_
5	Unidos	_	PROPN	_	_	4	flat	_	_
6	transfirió	_	VERB	_	_	0	root	_	_
7	ayer	_	ADV	_	_	6	advmod	_	_
8	formalmente	_	ADV	_	_	7	advmod	_	_
9	la	_	DET	_	_	10	det	_	_
10	emisora	_	NOUN	_	_	6	obj	_	_
11	de	_	ADP	_	_	12	case	_	_
12	Radio	_	PROPN	_	_	10	nmod	_	_
13	Liberty	_	PROPN	_	_	12	flat	_	_
14	a	_	ADP	_	_	15	case	_	_
15	Radio	_	PROPN	_	_	7	obl:arg	_	_
16	Nacional	_	PROPN	_	_	15	flat	_	_
17	de	_	ADP	_	_	18	case	_	_
18	España	_	PROPN	_	_	15	flat	_	_
19	,	_	PUNCT	_	_	22	

### REMOVE Sentences With Cycle 

In [24]:
# Remove trees with cycles 
dec_trees = [ele for idx, ele in enumerate(dec_trees) if idx not in tree_cycles_ids]
#print(len(dec_trees))

# print trees with cycles 
for item in tree_cycles:
    print(item)

1	Afortunadamente	_	ADV	_	_	13	advmod	_	_
2	para	_	ADP	_	_	1	case	_	_
3	nosotros	_	PRON	_	_	1	nmod	_	_
4	,	_	PUNCT	_	_	8	punct	_	_
5	y	_	CCONJ	_	_	8	cc	_	_
6	para	_	ADP	_	_	8	case	_	_
7	nuestro	_	DET	_	_	8	det	_	_
8	baloncesto	_	NOUN	_	_	3	conj	_	_
9	,	_	PUNCT	_	_	3	punct	_	_
10	ahora	_	ADV	_	_	20	advmod	_	_
11	las	_	DET	_	_	12	det	_	_
12	opiniones	_	NOUN	_	_	26	nsubj	_	_
13	en	_	ADP	_	_	17	case	_	_
14	contra	_	NOUN	_	_	13	fixed	_	_
15	de	_	ADP	_	_	13	fixed	_	_
16	una	_	DET	_	_	17	det	_	_
17	defensa	_	NOUN	_	_	12	nmod	_	_
18	agresiva	_	ADJ	_	_	17	amod	_	_
19	en	_	ADP	_	_	23	case	_	_
20	relación	_	NOUN	_	_	19	fixed	_	_
21	con	_	ADP	_	_	19	fixed	_	_
22	una	_	DET	_	_	23	det	_	_
23	defensa	_	NOUN	_	_	18	nmod	_	_
24	pasiva	_	ADJ	_	_	23	punct	_	_
25	ya	_	ADV	_	_	28	advmod	_	_
26	no	_	ADV	_	_	1	advmod	_	_
27	son	_	AUX	_	_	26	cop	_	_
28	unánimes	_	ADJ	_	_	27	punct	_	_
29	como	_	SCONJ	_	_	30	mark	_	_
30	hace	_	VERB	_	_	28	advcl	_	_
31	unos	_	DET	_	_	32	det	_	_
32	años	_	NOUN	_	_	30	obj	_	_
33	.

### Decoded Gold Trees from the Test Dataset

In [25]:
gold_dec_trees = []
for gold_tree in test_trees:
    d_tree_gold = D_Tree.from_string(gold_tree)

    encoder = D_NaiveRelativeEncoding(separator="_", hang_from_root=True)
    #print("\n[*] Linearized tree:")
    ld_tree_gold = encoder.encode(d_tree_gold)

    #print("\n[*] Decoded tree:")
    d_tree_gold = encoder.decode(ld_tree_gold)
    d_tree_gold.postprocess_tree(search_root_strat=D_ROOT_HEAD, allow_multi_roots=False)
    
    d_tree_gold = str(d_tree_gold)
    gold_dec_trees.append(d_tree_gold)
    print(d_tree_gold)

1	Partidario	_	ADJ	_	_	17	amod	_	_
2	de	_	ADP	_	_	5	case	_	_
3	la	_	DET	_	_	5	det	_	_
4	"	_	PUNCT	_	_	5	punct	_	_
5	perestroika	_	NOUN	_	_	1	nmod	_	_
6	"	_	PUNCT	_	_	5	punct	_	_
7	de	_	ADP	_	_	8	case	_	_
8	Mijail	_	PROPN	_	_	5	nmod	_	_
9	Gorbachov	_	PROPN	_	_	8	flat	_	_
10	en	_	ADP	_	_	12	case	_	_
11	la	_	DET	_	_	12	det	_	_
12	Unión	_	PROPN	_	_	5	nmod	_	_
13	Soviética	_	PROPN	_	_	12	flat	_	_
14	,	_	PUNCT	_	_	1	punct	_	_
15	en	_	ADP	_	_	16	case	_	_
16	1989	_	NOUN	_	_	17	obl	_	_
17	entró	_	VERB	_	_	0	root	_	_
18	en	_	ADP	_	_	19	case	_	_
19	conflicto	_	NOUN	_	_	17	obl	_	_
20	con	_	ADP	_	_	21	case	_	_
21	Yívkov	_	PROPN	_	_	17	obl	_	_
22	,	_	PUNCT	_	_	23	punct	_	_
23	líder	_	NOUN	_	_	21	appos	_	_
24	durante	_	ADP	_	_	26	case	_	_
25	35	_	NUM	_	_	26	nummod	_	_
26	años	_	NOUN	_	_	23	nmod	_	_
27	de	_	ADP	_	_	29	case	_	_
28	el	_	DET	_	_	29	det	_	_
29	Partido	_	PROPN	_	_	23	nmod	_	_
30	Comunista	_	PROPN	_	_	29	flat	_	_
31	y	_	CCONJ	_	_	34	cc	_	_
32	de	_	ADP	_	_	34	case	_	_
33	el	_	DET	_	_	34	det	

1	Las	_	DET	_	_	2	det	_	_
2	primarias	_	ADJ	_	_	5	nsubj	_	_
3	presidenciales	_	ADJ	_	_	2	amod	_	_
4	estadounidenses	_	ADJ	_	_	2	amod	_	_
5	continúan	_	VERB	_	_	0	root	_	_
6	hoy	_	ADV	_	_	5	advmod	_	_
7	en	_	ADP	_	_	9	case	_	_
8	tres	_	NUM	_	_	9	nummod	_	_
9	estados	_	NOUN	_	_	5	obl	_	_
10	,	_	PUNCT	_	_	25	punct	_	_
11	a	_	ADP	_	_	25	mark	_	_
12	pesar	_	NOUN	_	_	11	fixed	_	_
13	de	_	ADP	_	_	11	fixed	_	_
14	que	_	SCONJ	_	_	11	fixed	_	_
15	el	_	DET	_	_	16	det	_	_
16	demócrata	_	NOUN	_	_	25	nsubj	_	_
17	Albert	_	PROPN	_	_	16	appos	_	_
18	Gore	_	PROPN	_	_	17	flat	_	_
19	y	_	CCONJ	_	_	21	cc	_	_
20	el	_	DET	_	_	21	det	_	_
21	republicano	_	NOUN	_	_	16	conj	_	_
22	George	_	PROPN	_	_	21	appos	_	_
23	W.	_	PROPN	_	_	22	flat	_	_
24	Bush	_	PROPN	_	_	22	flat	_	_
25	tienen	_	VERB	_	_	5	advcl	_	_
26	casi	_	ADV	_	_	27	advmod	_	_
27	asegurada	_	ADJ	_	_	25	obj	_	_
28	su	_	DET	_	_	29	det	_	_
29	candidatura	_	NOUN	_	_	25	obj	_	_
30	a	_	ADP	_	_	32	case	_	_
31	la	_	DET	_	_	32	det	_	_
32	Casa	_	PROPN	_	_	29	nm

1	Fuentes	_	NOUN	_	_	14	nsubj	_	_
2	de	_	ADP	_	_	4	case	_	_
3	el	_	DET	_	_	4	det	_	_
4	Hospital	_	PROPN	_	_	1	nmod	_	_
5	La	_	DET	_	_	6	det	_	_
6	Paz	_	PROPN	_	_	4	flat	_	_
7	,	_	PUNCT	_	_	11	punct	_	_
8	cuyo	_	DET	_	_	9	nmod	_	_
9	jefe	_	NOUN	_	_	11	nsubj	_	_
10	es	_	AUX	_	_	11	cop	_	_
11	Carlos	_	PROPN	_	_	1	acl	_	_
12	Villasante	_	PROPN	_	_	11	flat	_	_
13	,	_	PUNCT	_	_	11	punct	_	_
14	indicaron	_	VERB	_	_	0	root	_	_
15	que	_	SCONJ	_	_	20	mark	_	_
16	hasta	_	ADP	_	_	17	case	_	_
17	hoy	_	ADV	_	_	20	advmod	_	_
18	no	_	ADV	_	_	20	advmod	_	_
19	podían	_	AUX	_	_	20	aux	_	_
20	dar	_	VERB	_	_	14	xcomp	_	_
21	información	_	NOUN	_	_	20	obj	_	_
22	sobre	_	ADP	_	_	24	case	_	_
23	el	_	DET	_	_	24	det	_	_
24	caso	_	NOUN	_	_	21	nmod	_	_
25	.	_	PUNCT	_	_	14	punct	_	_


1	En	_	ADP	_	_	2	case	_	_
2	Vigo	_	PROPN	_	_	39	obl	_	_
3	,	_	PUNCT	_	_	2	punct	_	_
4	los	_	DET	_	_	5	det	_	_
5	familiares	_	NOUN	_	_	39	nsubj	_	_
6	de	_	ADP	_	_	8	case	_	_
7	un	_	DET	_	_	8	det	_	_
8	anciano	_	NOUN	_	_	5	nmod	_	_
9	de

In [26]:
# Remove trees (with cycles) to make it consistent with predicted trees
gold_dec_trees = [ele for idx, ele in enumerate(gold_dec_trees) if idx not in tree_cycles_ids]
#print(len(gold_dec_trees))

### Write Decoded Trees into Files (gold, predicted)

In [27]:
gold_file_path = "../datasets/UD_Spanish-AnCora/gold-trees-test-decoded-rel.conllu"
# Delete previous files to avoid appending records again
if os.path.isfile(gold_file_path):
    os.remove(gold_file_path)
for t in gold_dec_trees:
    write_to_file(t, gold_file_path)

pred_file_path = "../datasets/UD_Spanish-AnCora//model-predictions-test-decoded-rel.conllu"
# Delete previous files to avoid appending records again
if os.path.isfile(pred_file_path):
    os.remove(pred_file_path)
for t in dec_trees:
    write_to_file(t, pred_file_path)

### Evaluate Model Performance using conll18_ud_eval.py

In [28]:
import subprocess

# Define the paths to the gold-standard and system-generated CoNLL-U files
gold_file = "../datasets/UD_Spanish-AnCora//gold-trees-test-decoded-rel.conllu"
system_file = "../datasets/UD_Spanish-AnCora//model-predictions-test-decoded-rel.conllu"

# Run the conll18_ud_eval.py script using subprocess
command = ["python", "/eval/conll18_ud_eval.py", gold_file, system_file]
result = subprocess.run(command, stdout=subprocess.PIPE, stderr=subprocess.PIPE, text=True)

# Print the evaluation results
print(result.stdout)

# Check for errors, if any
if result.returncode != 0:
    print("Error occurred:", result.stderr)

LAS F1 Score: 77.84
MLAS Score: 69.29
BLEX Score: 71.24

